<a href="https://colab.research.google.com/github/kocakcan/ml_foundations/blob/main/multi_headed_attention.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!pip install bertviz
from transformers import BertModel, BertTokenizer
from bertviz import head_view
import torch
import pandas as pd

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 157.5/157.5 kB 5.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 140.6/140.6 kB 10.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 14.5/14.5 MB 100.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 49.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 86.8/86.8 kB 3.3 MB/s eta 0:00:00


In [2]:
model = BertModel.from_pretrained("bert-base-uncased")

/usr/local/lib/python3.12/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/570 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/440M [00:00<?, ?B/s]

In [3]:
# Base BERT has 12 encoders in the encoder stack
len(model.encoder.layer)

12

In [4]:
model.encoder.layer[0]

BertLayer(
  (attention): BertAttention(
    (self): BertSdpaSelfAttention(
      (query): Linear(in_features=768, out_features=768, bias=True)
      (key): Linear(in_features=768, out_features=768, bias=True)
      (value): Linear(in_features=768, out_features=768, bias=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (output): BertSelfOutput(
      (dense): Linear(in_features=768, out_features=768, bias=True)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
  )
  (intermediate): BertIntermediate(
    (dense): Linear(in_features=768, out_features=3072, bias=True)
    (intermediate_act_fn): GELUActivation()
  )
  (output): BertOutput(
    (dense): Linear(in_features=3072, out_features=768, bias=True)
    (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
    (dropout): Dropout(p=0.1, inplace=False)
  )
)

In [5]:
model.encoder.layer[0].attention

BertAttention(
  (self): BertSdpaSelfAttention(
    (query): Linear(in_features=768, out_features=768, bias=True)
    (key): Linear(in_features=768, out_features=768, bias=True)
    (value): Linear(in_features=768, out_features=768, bias=True)
    (dropout): Dropout(p=0.1, inplace=False)
  )
  (output): BertSelfOutput(
    (dense): Linear(in_features=768, out_features=768, bias=True)
    (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
    (dropout): Dropout(p=0.1, inplace=False)
  )
)

In [6]:
# Loading vanilla BERT-base model
tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
model = BertModel.from_pretrained("bert-base-uncased")

tokenizer_config.json:   0%|          | 0.00/48.0 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

In [7]:
text = "My friend told me about this class and I love it so far! She was right."

tokens = tokenizer.encode(text)
# unsqueeze changes the shape from (20,) -> (1, 20)
inputs = torch.tensor(tokens).unsqueeze(0)
inputs

tensor([[ 101, 2026, 2767, 2409, 2033, 2055, 2023, 2465, 1998, 1045, 2293, 2009,
         2061, 2521,  999, 2016, 2001, 2157, 1012,  102]])

In [8]:
attention = model(inputs, output_attentions=True)[2]

BertSdpaSelfAttention is used but `torch.nn.functional.scaled_dot_product_attention` does not support non-absolute `position_embedding_type` or `output_attentions=True` or `head_mask`. Falling back to the manual attention implementation, but specifying the manual implementation will be required from Transformers version v5.0.0 onwards. This warning can be removed using the argument `attn_implementation="eager"` when loading the model.


In [9]:
# average attention in the last encoder
final_attention = attention[-1].mean(1)[0]

In [10]:
attention_df = pd.DataFrame(final_attention.detach()).map(float).round(3)

attention_df.columns = tokenizer.convert_ids_to_tokens(tokens)
attention_df.index = tokenizer.convert_ids_to_tokens(tokens)
attention_df


[CLS]     my  friend   told     me  about   this  class    and      i  \
[CLS]   0.092  0.028   0.019  0.011  0.012  0.022  0.050  0.087  0.031  0.023   
my      0.021  0.023   0.014  0.010  0.013  0.021  0.028  0.015  0.014  0.012   
friend  0.018  0.009   0.129  0.009  0.005  0.008  0.008  0.012  0.009  0.005   
told    0.010  0.004   0.013  0.084  0.004  0.011  0.005  0.005  0.005  0.002   
me      0.024  0.013   0.010  0.011  0.017  0.016  0.018  0.011  0.014  0.010   
about   0.019  0.010   0.007  0.018  0.010  0.079  0.021  0.012  0.012  0.006   
this    0.026  0.014   0.003  0.004  0.010  0.015  0.069  0.020  0.011  0.010   
class   0.028  0.010   0.007  0.006  0.006  0.015  0.029  0.096  0.010  0.009   
and     0.031  0.016   0.006  0.007  0.012  0.009  0.013  0.009  0.080  0.013   
i       0.023  0.014   0.008  0.005  0.011  0.011  0.019  0.012  0.021  0.029   
love    0.013  0.005   0.005  0.005  0.004  0.009  0.015  0.009  0.007  0.006   
it      0.025  0.008   0.004  0.005  0.008  0.014  0.047  0.021  0.012  0.008   
so      0.023  0.014   0.007  0.009  0.018  0.020  0.022  0.016  0.012  0.014   
far     0.017  0.009   0.008  0.009  0.013  0.019  0.024  0.017  0.016  0.011   
!       0.037  0.014   0.006  0.006  0.008  0.009  0.015  0.010  0.025  0.014   
she     0.032  0.011   0.030  0.023  0.007  0.007  0.008  0.011  0.016  0.008   
was     0.028  0.012   0.020  0.012  0.009  0.008  0.008  0.009  0.012  0.008   
right   0.053  0.008   0.005  0.005  0.006  0.006  0.006  0.004  0.006  0.006   
.       0.013  0.003   0.002  0.001  0.002  0.001  0.003  0.005  0.005  0.003   
[SEP]   0.014  0.004   0.002  0.001  0.002  0.002  0.003  0.006  0.005  0.003   

         love     it     so    far      !    she    was  right      .  [SEP]  
[CLS]   0.023  0.031  0.007  0.028  0.067  0.057  0.065  0.124  0.104  0.120  
my      0.010  0.023  0.011  0.009  0.016  0.022  0.021  0.019  0.312  0.388  
friend  0.009  0.006  0.004  0.005  0.009  0.023  0.010  0.006  0.314  0.401  
told    0.008  0.005  0.005  0.003  0.006  0.008  0.004  0.003  0.351  0.464  
me      0.010  0.014  0.007  0.008  0.014  0.009  0.006  0.005  0.347  0.436  
about   0.014  0.019  0.008  0.008  0.012  0.005  0.003  0.005  0.320  0.412  
this    0.011  0.018  0.006  0.008  0.012  0.005  0.003  0.004  0.331  0.421  
class   0.013  0.019  0.006  0.009  0.015  0.010  0.005  0.005  0.312  0.390  
and     0.010  0.010  0.008  0.009  0.024  0.014  0.012  0.011  0.316  0.386  
i       0.014  0.013  0.008  0.014  0.019  0.012  0.009  0.008  0.334  0.414  
love    0.105  0.010  0.007  0.012  0.010  0.004  0.003  0.005  0.336  0.432  
it      0.013  0.050  0.012  0.010  0.011  0.007  0.004  0.003  0.325  0.415  
so      0.021  0.028  0.042  0.017  0.018  0.008  0.009  0.007  0.312  0.383  
far     0.017  0.020  0.018  0.059  0.012  0.005  0.004  0.002  0.321  0.398  
!       0.015  0.008  0.007  0.009  0.050  0.010  0.011  0.012  0.332  0.402  
she     0.007  0.007  0.004  0.004  0.017  0.065  0.056  0.015  0.305  0.364  
was     0.006  0.008  0.006  0.005  0.016  0.055  0.117  0.025  0.290  0.346  
right   0.007  0.003  0.003  0.002  0.010  0.012  0.022  0.107  0.328  0.400  
.       0.002  0.002  0.001  0.002  0.007  0.004  0.002  0.002  0.413  0.527  
[SEP]   0.003  0.002  0.002  0.002  0.007  0.005  0.003  0.002  0.411  0.523

In [11]:
# Layer index 2 seems to be attending to the previous token
# Layer index 6 seems to be for pronouns
tokens_as_list = tokenizer.convert_ids_to_tokens(inputs[0])
head_view(attention, tokens_as_list)

<IPython.core.display.Javascript object>

In [12]:
# Head 3-1 attends to previous token
head_view(attention, tokenizer.convert_ids_to_tokens(inputs[0]), layer=2, heads=[0])

<IPython.core.display.Javascript object>

In [13]:
# Head 8-10 relating direct objects to their verbs e.g., told -> me
head_view(attention, tokenizer.convert_ids_to_tokens(inputs[0]), layer=7, heads=[9])

<IPython.core.display.Javascript object>

In [14]:
# Attention in the 8th encoder's 10th head to see direct object attention
eight_ten = attention[7][0][9]

In [15]:
# Get the attention matrix
attention_df = pd.DataFrame(eight_ten.detach()).map(float).round(3)

attention_df.columns = tokenizer.convert_ids_to_tokens(tokens)
attention_df.index = tokenizer.convert_ids_to_tokens(tokens)
attention_df

[CLS]     my  friend   told     me  about   this  class    and      i  \
[CLS]   0.007  0.004   0.005  0.002  0.001  0.001  0.003  0.004  0.002  0.001   
my      0.031  0.030   0.027  0.009  0.004  0.002  0.001  0.004  0.006  0.001   
friend  0.022  0.128   0.024  0.002  0.002  0.000  0.001  0.001  0.004  0.001   
told    0.035  0.072   0.014  0.013  0.005  0.002  0.002  0.002  0.002  0.000   
me      0.010  0.010   0.005  0.683  0.015  0.007  0.001  0.001  0.001  0.000   
about   0.017  0.015   0.025  0.222  0.024  0.015  0.011  0.020  0.005  0.001   
this    0.005  0.002   0.008  0.223  0.030  0.452  0.073  0.046  0.003  0.001   
class   0.012  0.002   0.004  0.074  0.020  0.204  0.339  0.138  0.004  0.001   
and     0.030  0.008   0.001  0.077  0.019  0.091  0.017  0.013  0.084  0.008   
i       0.022  0.016   0.008  0.181  0.018  0.021  0.003  0.007  0.363  0.033   
love    0.036  0.007   0.002  0.015  0.003  0.003  0.003  0.005  0.163  0.197   
it      0.004  0.001   0.005  0.069  0.003  0.170  0.018  0.020  0.023  0.041   
so      0.008  0.003   0.001  0.004  0.000  0.001  0.001  0.005  0.055  0.044   
far     0.013  0.008   0.002  0.004  0.002  0.001  0.009  0.002  0.059  0.098   
!       0.008  0.003   0.001  0.005  0.001  0.000  0.001  0.001  0.042  0.015   
she     0.004  0.003   0.002  0.002  0.000  0.000  0.000  0.001  0.008  0.002   
was     0.007  0.003   0.002  0.004  0.001  0.001  0.000  0.001  0.003  0.000   
right   0.021  0.004   0.002  0.004  0.001  0.000  0.001  0.001  0.005  0.001   
.       0.009  0.002   0.000  0.005  0.001  0.002  0.001  0.002  0.002  0.000   
[SEP]   0.015  0.006   0.003  0.003  0.003  0.003  0.006  0.004  0.007  0.004   

         love     it     so    far      !    she    was  right      .  [SEP]  
[CLS]   0.002  0.003  0.001  0.005  0.006  0.005  0.010  0.039  0.033  0.867  
my      0.001  0.002  0.001  0.002  0.033  0.002  0.002  0.004  0.050  0.788  
friend  0.001  0.001  0.000  0.002  0.016  0.001  0.002  0.001  0.025  0.765  
told    0.000  0.000  0.000  0.001  0.009  0.001  0.000  0.000  0.034  0.808  
me      0.000  0.000  0.000  0.000  0.003  0.000  0.001  0.003  0.004  0.255  
about   0.001  0.000  0.000  0.001  0.004  0.001  0.001  0.006  0.012  0.618  
this    0.002  0.001  0.001  0.002  0.001  0.000  0.000  0.007  0.001  0.143  
class   0.008  0.007  0.002  0.004  0.001  0.002  0.001  0.018  0.006  0.154  
and     0.002  0.001  0.001  0.001  0.009  0.001  0.002  0.003  0.022  0.610  
i       0.004  0.001  0.002  0.002  0.010  0.000  0.001  0.001  0.004  0.302  
love    0.036  0.006  0.003  0.003  0.004  0.001  0.001  0.001  0.008  0.502  
it      0.550  0.013  0.007  0.008  0.002  0.001  0.000  0.005  0.000  0.060  
so      0.067  0.008  0.005  0.019  0.008  0.002  0.000  0.001  0.001  0.767  
far     0.164  0.097  0.101  0.012  0.021  0.012  0.009  0.002  0.002  0.382  
!       0.004  0.006  0.013  0.014  0.045  0.010  0.004  0.004  0.004  0.818  
she     0.012  0.005  0.012  0.013  0.227  0.051  0.031  0.018  0.007  0.601  
was     0.010  0.001  0.003  0.030  0.204  0.182  0.051  0.043  0.017  0.438  
right   0.004  0.002  0.001  0.004  0.099  0.146  0.158  0.013  0.042  0.490  
.       0.001  0.001  0.001  0.006  0.039  0.047  0.054  0.133  0.111  0.582  
[SEP]   0.005  0.004  0.002  0.006  0.014  0.007  0.004  0.006  0.025  0.874